In [2]:
from pathlib import Path
from PIL import Image, ImageOps
import os

In [3]:
data_head_dir = Path('data/data/')
subdirs = [Path(subdir.stem) for subdir in data_head_dir.iterdir() if subdir.is_dir()]
src_image_ids = ['_'.join(a_path.name.split('_')[:3]) for a_path in subdirs]

In [5]:
import cv2
from pathlib import Path
import random
import numpy as np

# Define the data directory and the path to the text file
data_head_dir = Path('data/data/')
train_source_images_file = 'train_source_images.txt'

# Read the list of target image IDs from the text file
with open(train_source_images_file, 'r') as file:
    target_image_ids = [line.strip() for line in file]

# Define an augmentation function using OpenCV
def augment_image(image_path, output_dir, suffix='_augmented', num_augmentations=1):
    image = cv2.imread(str(image_path))
    image_name = image_path.stem

    for i in range(num_augmentations):
        augmented_image_name = f"{image_name}{suffix}_{i}.jpg"
        augmented_image_path = output_dir / augmented_image_name

        # Apply random transformations using OpenCV
        augmented_image = apply_random_transformations(image)

        # Save augmented image in the same directory as the original image
        cv2.imwrite(str(augmented_image_path), augmented_image)
        print(f"Saved augmented image: {augmented_image_path}")

# Define a function to apply random transformations using OpenCV
def apply_random_transformations(image):
    # Randomly crop the image
    h, w, _ = image.shape
    top = random.randint(0, h // 4)
    bottom = random.randint(3 * h // 4, h)
    left = random.randint(0, w // 4)
    right = random.randint(3 * w // 4, w)
    image = image[top:bottom, left:right, :]

    # Randomly zoom the image
    zoom_factor = random.uniform(0.8, 1.2)
    image = cv2.resize(image, None, fx=zoom_factor, fy=zoom_factor)

    # Randomly rotate the image
    rotation_angle = random.uniform(-10, 10)
    rotation_matrix = cv2.getRotationMatrix2D((w // 2, h // 2), rotation_angle, 1)
    image = cv2.warpAffine(image, rotation_matrix, (w, h))

    # Randomly adjust brightness and contrast
    alpha = random.uniform(0.8, 1.2)
    beta = random.uniform(-20, 20)
    image = cv2.convertScaleAbs(image, alpha=alpha, beta=beta)

    # Randomly translate the image
    tx = random.randint(-20, 20)
    ty = random.randint(-20, 20)
    translation_matrix = np.float32([[1, 0, tx], [0, 1, ty]])
    image = cv2.warpAffine(image, translation_matrix, (w, h))

    return image

# Iterate through subdirectories
for subdir in data_head_dir.iterdir():
    if subdir.is_dir():
        # Extract the first three components of the subdir name
        subdir_prefix = '_'.join(subdir.name.split('_')[:3])

        # Check if any of the target_image_ids is a partial match for subdir_prefix
        if any(image_id in subdir_prefix for image_id in target_image_ids):
            # Check if 'tiles' directory exists
            tiles_dir = subdir / 'tiles'
            if tiles_dir.is_dir():
                # Check if 'background' or 'frost' folder exists
                background = tiles_dir / 'background'
                if background.is_dir():
                    # Iterate through image files in the 'background' directory
                    for image_path in background.iterdir():
                        augment_image(image_path, background)

                frost = tiles_dir / 'frost'
                if frost.is_dir():
                    # Iterate through image files in the 'frost' directory
                    for image_path in frost.iterdir():
                        augment_image(image_path, frost)
                else:
                    print(f"Skipped: {frost} does not exist")

            else:
                print(f"Skipped: {tiles_dir} does not exist")


Saved augmented image: data\data\ESP_018002_1820_0_5120_20480_25600\tiles\background\ESP_018002_1820_0_598_22274_22872_augmented_0.jpg
Saved augmented image: data\data\ESP_018002_1820_0_5120_20480_25600\tiles\background\ESP_018002_1820_1196_1794_20480_21078_augmented_0.jpg
Saved augmented image: data\data\ESP_018002_1820_0_5120_20480_25600\tiles\background\ESP_018002_1820_1196_1794_21078_21676_augmented_0.jpg
Saved augmented image: data\data\ESP_018002_1820_0_5120_20480_25600\tiles\background\ESP_018002_1820_1196_1794_21676_22274_augmented_0.jpg
Saved augmented image: data\data\ESP_018002_1820_0_5120_20480_25600\tiles\background\ESP_018002_1820_1196_1794_22274_22872_augmented_0.jpg
Saved augmented image: data\data\ESP_018002_1820_0_5120_20480_25600\tiles\background\ESP_018002_1820_1794_2392_20480_21078_augmented_0.jpg
Saved augmented image: data\data\ESP_018002_1820_0_5120_20480_25600\tiles\background\ESP_018002_1820_1794_2392_21078_21676_augmented_0.jpg
Saved augmented image: data\dat